In [38]:

import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go
import itertools
import random
import requests
import os
import json
import time
import psutil

from sklearn.preprocessing import MinMaxScaler
from sklearn.decomposition import PCA
from sklearn.multioutput import MultiOutputRegressor
from sklearn.model_selection import train_test_split
from statsmodels.tsa.holtwinters import ExponentialSmoothing
from sklearn.metrics import mean_absolute_error, mean_squared_error, mean_absolute_percentage_error
from sklearn.ensemble import RandomForestRegressor
from xgboost import XGBRegressor
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import RandomizedSearchCV

In [39]:
local_base_dir = '../data'
data = {}

def addFolderAndReadAll(d_name):
    data[d_name] = {}
    folder_path = os.path.join(local_base_dir, d_name)
    
    if not os.path.exists(folder_path):
        print(f"Directory {folder_path} does not exist.")
        return 0

    csv_files = [f_name for f_name in os.listdir(folder_path) if f_name.endswith('.csv')]
    csvs_num = 0
    for f_name in csv_files:
        file_path = os.path.join(folder_path, f_name)
        df = pd.read_csv(file_path)
        data[d_name][f_name] = df
        csvs_num += 1
    return csvs_num

directories = ["artificialWithAnomaly", "artificialNoAnomaly", "realAdExchange", "realAWSCloudwatch", "realKnownCause", "realTraffic", "realTweets"]
csvs_num = sum([addFolderAndReadAll(d_name) for d_name in directories])

print(f"Total CSV files processed: {csvs_num}")


Total CSV files processed: 58


In [40]:
# Function to get a random start date from the DataFrame index
def get_random_start_date(index):
    return np.random.choice(index)

# Main function to repeat the process until non-None frequency is obtained
def find_non_none_frequency(df, offset=9):
    while True:
        # Get a random start date from the DataFrame index
        start_date = pd.to_datetime(get_random_start_date(df.index))

        # Find the index of the end date by moving 9 steps through the indices
        end_date_index = df.index.get_loc(start_date) + offset

        # Check if the end date index is within the range of the DataFrame index
        if end_date_index < len(df.index):
            # Calculate the end date using the index
            end_date = df.index[end_date_index]

            # Infer frequency within the specified date range
            subset_df = df.loc[start_date:end_date]
            freq = pd.infer_freq(subset_df.index)

            if freq is not None:
                print("Inferred frequency within range", start_date, "-", end_date, ":", freq)
                return freq  # Exit the loop and return the inferred frequency

In [41]:
def max_consecutive_missing_dates(inferred_freq, missing_dates):
    # Function to check if two dates are consecutive based on the inferred frequency
    def are_consecutive(date1, date2, freq):
        # Calculate the difference between dates based on the inferred frequency
        diff = date2 - date1
        # Check if the difference matches the frequency
        if freq == 'D':
            return diff.days == 1
        elif freq.endswith('H')| freq.endswith('h'):
             # If the frequency ends with 'H', check if it represents hourly intervals
            if freq[:-1]:  # Check if there is a multiplier
                  interval = int(freq[:-1])
                  return diff.total_seconds() == interval * 3600
            else:
                   # If no multiplier is provided, it's assumed to be one hour
                   return diff.total_seconds() == 3600
        elif freq.endswith('T') | freq.endswith('min') :
            if freq.endswith('T'):
                # Extract the interval from the frequency string
                interval = int(freq[:-1])
                return diff.seconds // 60 == interval
            else:
                interval = int(freq[:-3])
                return diff.seconds // 60 == interval
        else:
            raise ValueError("Unsupported frequency: {}".format(freq))

    # Initialize variables to track maximum length and current length
    max_consecutive_missing = 0
    current_consecutive_missing = 0

    # Iterate over the missing dates
    for i in range(1, len(missing_dates)):
        # Check if the current date is consecutive with the previous date
        if are_consecutive(missing_dates[i - 1], missing_dates[i], inferred_freq):
            # Increment current consecutive missing count
            current_consecutive_missing += 1
        else:
            # Update maximum consecutive missing count if needed
            max_consecutive_missing = max(max_consecutive_missing, current_consecutive_missing)
            # Reset current consecutive missing count
            current_consecutive_missing = 0

    # Update max_consecutive_missing if current_consecutive_missing is still greater
    max_consecutive_missing = max(max_consecutive_missing, current_consecutive_missing)

    return max_consecutive_missing

In [42]:
def preprocess(df, f_name):
    # Convert 'timestamp' column to datetime format and rename it to 'ds'
    df['timestamp'] = pd.to_datetime(df['timestamp'])

    # Removing the duplicate rows
    df = df[~df.duplicated(keep='first')]

    duplicated_dates_length = len(df[df['timestamp'].duplicated(keep=False)])

    if  duplicated_dates_length > 0:
      print("Number of Duplicated Dates in "+ f_name + ": "+ str(duplicated_dates_length))
      # To make the mean as the value for the numerical columns if there are different values for a particular date
      df = df.groupby('timestamp').mean()
      # Reset index to bring 'timestamp' column back
      df.reset_index(inplace=True)

    df.set_index(['timestamp'], inplace=True)
    df.sort_index()

    # Create a date range with hourly frequency covering the entire time range
    start_date = df.index.min()
    end_date = df.index.max()

    #inferred_freq = pd.infer_freq(df.index)
    inferred_freq = find_non_none_frequency(df)

    if inferred_freq is None:
      inferred_freq = default_freq # setting the default frequency
      print("Cannot infer the frequency of the timestamp of the dataset "+ f_name+ " .Therefore the default frequency of " + default_freq+ " will be used")

    expected_date_range = pd.date_range(start=start_date, end=end_date, freq=inferred_freq)

    # Find the missing date entries
    missing_dates = expected_date_range[~expected_date_range.isin(df.index)]
    # Print or work with the list of missing dates
    print("Number of Missing Dates in "+ f_name + ": "+ str(len(missing_dates))+"\n")

    if len(missing_dates) > 0:
      df = df.asfreq(inferred_freq)
      df.sort_index()

      # Call the function with inferred_freq and missing_dates parameters
      max_consecutive = max_consecutive_missing_dates(inferred_freq, missing_dates)
      print("Maximum length of consecutive missing dates:", max_consecutive)
      if max_consecutive > 3:
        print("It is better to use other imputation method rather than linear interpolation")

      df['value'] = df['value'].interpolate(method='linear')

    return df

In [43]:
url = 'https://raw.githubusercontent.com/numenta/NAB/master/labels/combined_labels.json'

response = requests.get(url)

if response.status_code == 200:
    labels = json.loads(response.text)
else:
    print("Failed to retrieve data from the URL:", response.status_code)

In [44]:
# List of directories
dirs = ['realAdExchange', 'realAWSCloudwatch', 'realKnownCause', 'realTweets', 'artificialWithAnomaly', 'artificialNoAnomaly', 'realTraffic']
#dirs = ['realAdExchange']
#dirs = ['artificialNoAnomaly']

# Loop through each directory
for dir in dirs:
    for f_name in data[dir]:
        print("")
        print(f"Iterating over file: {dir} / {f_name}")
        df = preprocess(data[dir][f_name], f_name)
        labels_of_one_file = labels[dir+'/'+f_name]
        df['is_anomaly'] = 0
        for anomalous_timestamp in labels_of_one_file:
            anomalous_timestamp = pd.to_datetime(anomalous_timestamp)
            try:
                df.at[anomalous_timestamp, 'is_anomaly'] = 1  # Set is_anomaly to 1 at the index location
            except KeyError:
                print(f"Anomalous timestamp {anomalous_timestamp} not found in data[{dir}][{f_name}].")
                pass
        data[dir][f_name] = df  # Assign the modified DataFrame back to the data dictionary


Iterating over file: realAdExchange / exchange-2_cpm_results.csv
Number of Duplicated Dates in exchange-2_cpm_results.csv: 2
Inferred frequency within range 2011-07-16 15:00:01 - 2011-07-17 00:00:01 : h
Number of Missing Dates in exchange-2_cpm_results.csv: 25

Maximum length of consecutive missing dates: 19
It is better to use other imputation method rather than linear interpolation

Iterating over file: realAdExchange / exchange-3_cpc_results.csv
Inferred frequency within range 2011-08-06 17:15:01 - 2011-08-07 02:15:01 : h
Number of Missing Dates in exchange-3_cpc_results.csv: 109

Maximum length of consecutive missing dates: 14
It is better to use other imputation method rather than linear interpolation

Iterating over file: realAdExchange / exchange-4_cpm_results.csv
Inferred frequency within range 2011-09-01 15:15:01 - 2011-09-02 00:15:01 : h
Number of Missing Dates in exchange-4_cpm_results.csv: 4

Maximum length of consecutive missing dates: 0

Iterating over file: realAdExchan

In [45]:
# Specify the directory and file name
dir = 'realAWSCloudwatch'
f_name = 'ec2_cpu_utilization_ac20cd.csv'


# Retrieve the DataFrame
df = data[dir][f_name]

In [46]:
# Define the date to crop the DataFrame
cutoff_date = pd.Timestamp('2014-04-15')

# Filter the DataFrame using the index and store it back to the same variable
df = df[df.index <= cutoff_date]

# Store the filtered DataFrame back into the dictionary
data[dir][f_name] = df


In [47]:
f_name = 'ec2_cpu_utilization_5f5533.csv'

# Retrieve the DataFrame
df = data[dir][f_name]

In [48]:
# Define the date to crop the DataFrame
cutoff_date = pd.Timestamp('2014-02-25')

# Filter the DataFrame using the index and store it back to the same variable
df = df[df.index <= cutoff_date]

# Store the filtered DataFrame back into the dictionary
data[dir][f_name] = df

In [49]:
f_name = 'grok_asg_anomaly.csv'

# Retrieve the DataFrame
df = data[dir][f_name]

In [50]:
# Define the date to crop the DataFrame
cutoff_date = pd.Timestamp('2014-01-29')

# Filter the DataFrame using the index and store it back to the same variable
df = df[df.index <= cutoff_date]

# Store the filtered DataFrame back into the dictionary
data[dir][f_name] = df

In [51]:
f_name = 'rds_cpu_utilization_cc0c53.csv'

# Retrieve the DataFrame
df = data[dir][f_name]

In [52]:
# Define the date to crop the DataFrame
cutoff_date = pd.Timestamp('2014-02-25')

# Filter the DataFrame using the index and store it back to the same variable
df = df[df.index <= cutoff_date]

# Store the filtered DataFrame back into the dictionary
data[dir][f_name] = df

In [53]:
def split_data(df, train_ratio=0.6):
    train_size = int(len(df) * train_ratio)
    train, val = df[:train_size], df[train_size:]
    return train, val

In [54]:
# Create an empty DataFrame with the desired columns
original_values_df = pd.DataFrame(columns=['dir', 'values'])

for dir in dirs:
    print(f"Iterating over directory: {dir}")

    # Iterate over each file in the current directory
    for file_name in data[dir]:
        df = data[dir][file_name]
        if dir == 'realTraffic':
            df = df.dropna()
        # Assuming df is defined somewhere in the loop
        train, val = split_data(df)

        # Create a new row with the directory and values as a list
        new_row = pd.DataFrame({'dir': [dir], 'file_name':[file_name], 'values': [val['value'].tolist()]})

        # Concatenate the new row to the original_values_df
        original_values_df = pd.concat([original_values_df, new_row], ignore_index=True)


original_values_df

Iterating over directory: realAdExchange
Iterating over directory: realAWSCloudwatch
Iterating over directory: realKnownCause
Iterating over directory: realTweets
Iterating over directory: artificialWithAnomaly
Iterating over directory: artificialNoAnomaly
Iterating over directory: realTraffic


dir                                             values  \
0          realAdExchange  [0.160230773158, 0.210830475115, 0.28622422434...   
1          realAdExchange  [0.0970408163265, 0.0936600833484, 0.094246275...   
2          realAdExchange  [0.428944811047, 0.469532759242, 0.45564022899...   
3          realAdExchange  [0.0737386325362, 0.0840131819846, 0.079394993...   
4          realAdExchange  [0.0848198198198, 0.0985912823752, 0.111722365...   
5          realAdExchange  [0.56535245238, 0.545612490685, 0.521651179882...   
6       realAWSCloudwatch  [0.102, 0.102, 81.468, 98.67, 60.688, 87.11200...   
7       realAWSCloudwatch  [5.834, 7.066, 5.856, 6.228, 5.636, 6.058, 5.8...   
8       realAWSCloudwatch  [47.018, 43.004, 41.066, 44.554, 43.284, 42.12...   
9       realAWSCloudwatch  [219840.0, 209992.0, 215690.0, 182444.0, 21823...   
10      realAWSCloudwatch  [1.834, 2.042, 1.8, 1.826, 1.764, 1.7380000000...   
11      realAWSCloudwatch  [3376556.8, 2932539.4, 3868952.0, 4180022.4, 2...   
12      realAWSCloudwatch  [113.0, 12.0, 10.0, 53.0, 61.0, 6.0, 17.0, 36....   
13      realAWSCloudwatch  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
14      realAWSCloudwatch  [42.0, 121.2, 68.4, 42.0, 94.8, 68.4, 60.0, 68...   
15      realAWSCloudwatch  [0.132, 0.066, 0.2, 0.132, 0.134, 0.132, 0.066...   
16      realAWSCloudwatch  [0.0, 0.0, 63275800.0, 69726200.0, 156096000.0...   
17      realAWSCloudwatch  [34.6, 36.854, 35.822, 34.226, 39.906, 30.83, ...   
18      realAWSCloudwatch  [17.32, 17.0975, 17.5025, 16.6825, 17.9175, 16...   
19      realAWSCloudwatch  [88.666, 89.772, 87.516, 90.374, 87.458, 93.87...   
20      realAWSCloudwatch  [2.332, 2.022, 2.278, 3.33, 2.262, 2.038000000...   
21      realAWSCloudwatch  [0.132, 0.066, 0.068, 0.066, 0.066, 0.134, 0.0...   
22      realAWSCloudwatch  [33.446, 33.446, 35.8314, 35.7143, 35.9521, 30...   
23         realKnownCause  [32.165, 31.501, 29.165, 34.947, 43.881, 92.83...   
24         realKnownCause  [46.878, 44.824, 40.962, 44.24800000000001, 44...   
25         realKnownCause  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
26         realKnownCause  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
27         realKnownCause  [73.41217429, 72.83454005, 73.5939262, 72.7640...   
28         realKnownCause  [18308, 14352, 11746, 9042, 7318, 6009, 5364, ...   
29         realKnownCause  [88.61211764, 89.1473961, 91.03478432, 91.3025...   
30             realTweets  [3, 4, 1, 4, 6, 3, 3, 2, 3, 2, 5, 3, 3, 6, 4, ...   
31             realTweets  [2, 2, 3, 1, 3, 1, 0, 2, 0, 1, 1, 1, 2, 2, 2, ...   
32             realTweets  [124, 96, 89, 108, 121, 102, 109, 91, 69, 97, ...   
33             realTweets  [0, 3, 1, 1, 1, 2, 1, 0, 0, 0, 0, 0, 18, 1, 0,...   
34             realTweets  [10, 9, 6, 8, 4, 5, 10, 8, 10, 11, 17, 5, 8, 8...   
35             realTweets  [82, 113, 97, 103, 117, 91, 106, 94, 96, 95, 8...   
36             realTweets  [28, 41, 49, 26, 33, 41, 23, 42, 27, 55, 39, 2...   
37             realTweets  [0, 0, 0, 1, 0, 1, 0, 0, 1, 0, 0, 0, 4, 1, 1, ...   
38             realTweets  [37, 21, 16, 19, 24, 21, 20, 16, 27, 20, 26, 1...   
39             realTweets  [3, 3, 0, 2, 0, 2, 0, 6, 7, 6, 2, 5, 4, 5, 6, ...   
40  artificialWithAnomaly  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
41  artificialWithAnomaly  [69.22031202630001, 71.9084009857, 61.81713063...   
42  artificialWithAnomaly  [66.3469378498, 65.6693715131, 67.7255544671, ...   
43  artificialWithAnomaly  [54.7542395242, 64.0910791376, 63.3589509425, ...   
44  artificialWithAnomaly  [66.795532829, 73.7369493356, 67.9940474315, 7...   
45  artificialWithAnomaly  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
46    artificialNoAnomaly  [80.0, 80.0, 80.0, 80.0, 80.0, 80.0, 80.0, 80....   
47    artificialNoAnomaly  [68.0, 68.0, 68.0, 68.0, 68.0, 77.6, 77.6, 77....   
48    artificialNoAnomaly  [45.0, 45.0, 45.0, 45.0, 45.0, 45.0, 45.0, 45....   
49    artificialNoAnom

Loading of datasets (time series extracted features)

In [55]:
df = pd.read_csv('../dataset_preparation/ranking_dataset.csv')
df.head() 

unique_id     hurst  series_length  \
0         artificialNoAnomaly/art_daily_no_noise.csv       NaN           4032   
1  artificialNoAnomaly/art_daily_perfect_square_w...       NaN           4032   
2      artificialNoAnomaly/art_daily_small_noise.csv  0.412716           4032   
3                  artificialNoAnomaly/art_noisy.csv  0.507001           4032   
4     artificialWithAnomaly/art_daily_flatmiddle.csv  0.501646           4032   

   unitroot_pp  unitroot_kpss      hw_alpha       hw_beta      hw_gamma  \
0   -45.198782       0.046765  5.000000e-01  1.000000e-04  2.500000e-01   
1   -63.887428       0.043267  5.000000e-01  1.750000e-01  2.000000e-01   
2   -57.839587       0.046790  1.490000e-08  1.010000e-08  3.110000e-21   
3 -4126.670693       0.299753  1.580000e-08  7.610000e-09  2.480000e-06   
4   -49.327420       0.121571  5.372404e-01  1.590000e-07  2.630000e-07   

      stability  nperiods  ...  diff2_acf1  diff2_acf10  seas_acf1  \
0  1.050000e-62         1  ...   -0.500000     0.250000   0.928571   
1  0.000000e+00         1  ...   -0.500000     0.250000   0.928571   
2  1.280000e-05         1  ...   -0.620340     0.418001   0.918527   
3  5.353556e-03         1  ...   -0.676908     0.497557   0.005106   
4  1.456821e-02         1  ...   -0.553618     0.314774   0.833093   

   exponential_smoothing    xgboost  random_forest       gru        vae  \
0              26.762319   0.012269       0.003747  0.609464   1.559429   
1              27.341756   0.010629       0.000028  0.558414   1.410600   
2              25.923756   2.283104       2.199849  2.599541   3.569074   
3               2.800236   2.785615       2.883937  2.823385   2.805615   
4              39.576025  10.404284      10.448658  7.000000  14.631948   

       lstm        gan  
0  0.707946  10.602318  
1  0.414601   3.206596  
2  2.668343   5.901315  
3  2.778922   3.105839  
4  4.452525   8.156758  

[5 rows x 50 columns]

In [56]:
predicted_df_final = pd.read_csv('../dataset_preparation/predicted_results.csv')
predicted_df_final.head()

dir                               file_name  \
0         realKnownCause  ambient_temperature_system_failure.csv   
1  artificialWithAnomaly                art_daily_flatmiddle.csv   
2  artificialWithAnomaly                 art_daily_jumpsdown.csv   
3  artificialWithAnomaly                   art_daily_jumpsup.csv   
4    artificialNoAnomaly                  art_daily_no_noise.csv   

                                      original_value  \
0  [73.41217429 72.83454005 73.5939262  ... 72.04...   
1  [ 54.75423952  64.09107914  63.35895094 ... -2...   
2  [69.22031203 71.90840099 61.81713064 ... 19.59...   
3  [66.79553283 73.73694934 67.99404743 ... 20.56...   
4  [68.      68.      68.      ... 20.00384 20.00...   

                               exponential_smoothing  \
0  [73.77850842954233, 73.20902976953136, 72.0610...   
1  [32.15306197201045, 33.26697596156033, 31.7276...   
2  [51.35943000159044, 50.18172659028332, 51.9492...   
3  [52.994417842052655, 55.09202082580159, 56.767...   
4  [50.15540275732831, 50.33636061688616, 50.4992...   

                                             xgboost  \
0  [74.10153198242188, 73.49702453613281, 72.5597...   
1  [61.475990295410156, 61.475990295410156, 61.47...   
2  [67.20659637451172, 67.20659637451172, 67.2065...   
3  [67.72393798828125, 67.72393798828125, 67.7239...   
4  [67.99688720703125, 67.99688720703125, 67.9968...   

                                       random_forest  \
0  [74.56356811523438, 74.153076171875, 73.547012...   
1  [61.823387145996094, 61.823387145996094, 61.82...   
2  [66.29618072509766, 66.29618072509766, 66.2961...   
3  [66.1158447265625, 66.1158447265625, 66.115844...   
4  [67.99630737304688, 67.99630737304688, 67.9963...   

                                                lstm  \
0  [74.68119812011719, 74.13858795166016, 73.5678...   
1  [63.68165588378906, 61.994789123535156, 63.026...   
2  [65.81879425048828, 67.55445861816406, 67.8981...   
3  [69.51910400390625, 68.38858795166016, 69.9029...   
4  [67.0814437866211, 67.08610534667969, 66.90905...   

                                                 gru  \
0  [74.46144104003906, 73.89588928222656, 73.2900...   
1  [61.77735137939453, 56.6450309753418, 58.89463...   
2  [67.36017608642578, 65.58143615722656, 67.3408...   
3  [68.04312896728516, 68.07539367675781, 71.0043...   
4  [68.9959487915039, 68.95393371582031, 69.02851...   

                                                 vae  \
0  [73.41217429, 72.83454005, 73.5939262, 72.7640...   
1  [54.7542395242, 64.0910791376, 63.358950942500...   
2  [69.22031202630001, 71.9084009857, 61.81713063...   
3  [66.795532829, 73.7369493356, 67.9940474315, 7...   
4  [68.0, 68.0, 68.0, 68.0, 68.0, 77.6, 77.6, 77....   

                                                 gan  
0  [73.41217803955078, 72.83454132080078, 73.5939...  
1  [54.754241943359375, 64.09107971191406, 63.358...  
2  [69.2203140258789, 71.90840148925781, 61.81713...  
3  [66.7955322265625, 73.73695373535156, 67.99404...  
4  [68.0, 68.0, 68.0, 68.0, 68.0, 77.599998474121...

In [73]:
# # Calculate the length of each array in the specified columns for each row
# lengths_df = predicted_df_final[['file_name', 'exponential_smoothing', 'xgboost', 'random_forest', 'vae' ,'lstm', 'gru','gan']].copy()
# # Define a function to calculate length of the array (if not null)
# def get_length(arr):
#     try:
#         return len(eval(arr)) if isinstance(arr, str) else len(arr)
#     except:
#         return None
# # Apply the function to each column and store the results
# for column in ['exponential_smoothing', 'xgboost', 'random_forest', 'vae' ,'lstm', 'gru','gan']:
#     lengths_df[column] = lengths_df[column].apply(get_length)
# # Display the resulting DataFrame with array lengths
# lengths_df

In [58]:
predicted_df_final.tail()

dir                file_name           original_value  \
52  realTweets  Twitter_volume_GOOG.csv  [28 41 49 ... 32 72 72]   
53  realTweets   Twitter_volume_IBM.csv        [3 3 0 ... 2 2 1]   
54  realTweets    Twitter_volume_KO.csv  [10  9  6 ...  6 10 20]   
55  realTweets   Twitter_volume_PFE.csv        [0 3 1 ... 1 0 0]   
56  realTweets   Twitter_volume_UPS.csv        [2 2 3 ... 2 3 3]   

                                exponential_smoothing  \
52  [41.86992093420115, 31.210437979084002, 27.225...   
53  [3.779204033784743, 2.5627807886497447, 3.7628...   
54  [10.054217819414447, 10.878895170087135, 11.51...   
55  [1.007458957706923, 0.8121318334469377, 0.5998...   
56  [4.1480600777675845, 4.552850299328354, 4.7878...   

                                              xgboost  \
52  [31.05492401123047, 31.05492401123047, 31.0549...   
53  [2.3532228469848633, 2.3532228469848633, 2.353...   
54  [17.559114456176758, 17.559114456176758, 17.55...   
55  [0.8084390163421631, 0.8084390163421631, 0.808...   
56  [3.95580792427063, 2.8894946575164795, 2.88949...   

                                        random_forest  \
52  [43.99571228027344, 43.99571228027344, 43.9957...   
53  [2.332641839981079, 2.332641839981079, 2.33264...   
54  [9.550631523132324, 9.550631523132324, 9.55063...   
55  [0.832390546798706, 0.832390546798706, 0.83239...   
56  [3.5047826766967773, 3.615247964859009, 3.6152...   

                                                 lstm  \
52  [40.01594924926758, 31.449296951293945, 36.798...   
53  [2.4284443855285645, 2.448848247528076, 2.5032...   
54  [10.72048282623291, 10.78191089630127, 10.4066...   
55  [0.0, 0.0, 0.1768699586391449, 0.1640459150075...   
56  [4.4308037757873535, 3.147231340408325, 3.1213...   

                                                  gru  \
52  [40.222232818603516, 33.40334701538086, 33.628...   
53  [2.834887742996216, 3.1977756023406982, 2.8475...   
54  [5.727309226989746, 6.010121822357178, 6.53356...   
55  [-0.01168664451688528, -0.01248796284198761, 0...   
56  [3.3996925354003906, 2.9843485355377197, 2.791...   

                                                  vae  \
52  [28.0, 41.0, 49.0, 26.0, 33.0, 41.0, 23.0, 42....   
53  [3.0, 3.0, 0.0, 2.0, 0.0, 2.0, 0.0, 6.0, 7.0, ...   
54  [10.0, 9.0, 6.0, 8.0, 4.0, 5.0, 10.0, 8.0, 10....   
55  [0.0, 3.0, 1.0, 1.0, 1.0, 2.0, 1.0, 0.0, 0.0, ...   
56  [2.0, 2.0, 3.0000000000000004, 1.0, 3.00000000...   

                                                  gan  
52  [28.0, 41.0, 49.0, 26.0, 33.0, 41.0, 23.0, 42....  
53  [3.0, 3.0, 0.0, 2.0, 0.0, 2.0, 0.0, 6.0, 7.0, ...  
54  [9.999999046325684, 9.0, 6.0, 8.0, 4.0, 4.9999...  
55  [0.0, 3.0, 1.0, 1.0, 1.0, 2.0, 1.0, 0.0, 0.0, ...  
56  [2.0, 2.0, 3.0, 1.0, 3.0, 1.0, 0.0, 2.0, 0.0, ...

In [59]:
#original_values_df = pd.read_csv('../dataset_preparation/original_values.csv')
#original_values_df.head()

In [60]:
mae_df_final = pd.read_csv('../dataset_preparation/mae_results.csv')
mae_df_final.head()

dir                               file_name  \
0         realKnownCause  ambient_temperature_system_failure.csv   
1  artificialWithAnomaly                art_daily_flatmiddle.csv   
2  artificialWithAnomaly                 art_daily_jumpsdown.csv   
3  artificialWithAnomaly                   art_daily_jumpsup.csv   
4    artificialNoAnomaly                  art_daily_no_noise.csv   

   exponential_smoothing    xgboost  random_forest      lstm       gru  \
0               4.476763   5.694003       6.423569  0.762435  0.714506   
1              39.576025  10.404284      10.448658  5.711104  7.000000   
2              23.361411   4.582154       4.653303  2.606714  2.488999   
3              29.809584   6.721797       6.677968  6.450866  4.868384   
4              26.762319   0.012269       0.003747  0.668905  0.609464   

         vae        gan  
0   1.296207   3.638117  
1  14.631948   8.156758  
2   5.955469   6.054995  
3   8.809650   7.485657  
4   1.559429  10.602318

In [61]:
mape_df_final = pd.read_csv('../dataset_preparation/mape_results.csv')
mape_df_final.head()

dir                               file_name  \
0         realKnownCause  ambient_temperature_system_failure.csv   
1  artificialWithAnomaly                art_daily_flatmiddle.csv   
2  artificialWithAnomaly                 art_daily_jumpsdown.csv   
3  artificialWithAnomaly                   art_daily_jumpsup.csv   
4    artificialNoAnomaly                  art_daily_no_noise.csv   

   exponential_smoothing     xgboost  random_forest          lstm  \
0               0.068108    0.086113       0.097005      0.011248   
1           76202.121797  239.927798       0.518448  39093.868480   
2               0.682943    0.114854       0.116390      0.065088   
3               1.038506    0.081276       0.082050      0.090935   
4               0.892341    0.000361       0.000109      0.016754   

            gru           vae           gan  
0      0.010484  1.935214e+00      0.010484  
1  37380.291150  8.791554e+06  37380.291150  
2      0.061917  1.792380e+01      0.061917  
3      0.082032  1.202339e+01      0.082032  
4      0.018290  4.812693e+00      0.018290

Ranking of base models based on the evaluation metrics

In [62]:
# Define a function to rank models based on MAE values for each row
def rank_models(row):
    mae_values = row[['exponential_smoothing','xgboost', 'random_forest', 'lstm' ,'gru', 'vae','gan']] # 
    #mae_values = row[['exponential_smoothing', 'xgboost', 'random_forest']]
    model_rank = mae_values.sort_values().index.tolist()
    return model_rank

In [63]:
# Apply the function to each row of the DataFrame
df['model_rank'] = df.apply(rank_models, axis=1)
df.head()

unique_id     hurst  series_length  \
0         artificialNoAnomaly/art_daily_no_noise.csv       NaN           4032   
1  artificialNoAnomaly/art_daily_perfect_square_w...       NaN           4032   
2      artificialNoAnomaly/art_daily_small_noise.csv  0.412716           4032   
3                  artificialNoAnomaly/art_noisy.csv  0.507001           4032   
4     artificialWithAnomaly/art_daily_flatmiddle.csv  0.501646           4032   

   unitroot_pp  unitroot_kpss      hw_alpha       hw_beta      hw_gamma  \
0   -45.198782       0.046765  5.000000e-01  1.000000e-04  2.500000e-01   
1   -63.887428       0.043267  5.000000e-01  1.750000e-01  2.000000e-01   
2   -57.839587       0.046790  1.490000e-08  1.010000e-08  3.110000e-21   
3 -4126.670693       0.299753  1.580000e-08  7.610000e-09  2.480000e-06   
4   -49.327420       0.121571  5.372404e-01  1.590000e-07  2.630000e-07   

      stability  nperiods  ...  diff2_acf10  seas_acf1  exponential_smoothing  \
0  1.050000e-62         1  ...     0.250000   0.928571              26.762319   
1  0.000000e+00         1  ...     0.250000   0.928571              27.341756   
2  1.280000e-05         1  ...     0.418001   0.918527              25.923756   
3  5.353556e-03         1  ...     0.497557   0.005106               2.800236   
4  1.456821e-02         1  ...     0.314774   0.833093              39.576025   

     xgboost  random_forest       gru        vae      lstm        gan  \
0   0.012269       0.003747  0.609464   1.559429  0.707946  10.602318   
1   0.010629       0.000028  0.558414   1.410600  0.414601   3.206596   
2   2.283104       2.199849  2.599541   3.569074  2.668343   5.901315   
3   2.785615       2.883937  2.823385   2.805615  2.778922   3.105839   
4  10.404284      10.448658  7.000000  14.631948  4.452525   8.156758   

                                          model_rank  
0  [random_forest, xgboost, gru, lstm, vae, gan, ...  
1  [random_forest, xgboost, lstm, gru, vae, gan, ...  
2  [random_forest, xgboost, gru, lstm, vae, gan, ...  
3  [lstm, xgboost, exponential_smoothing, vae, gr...  
4  [lstm, gru, gan, xgboost, random_forest, vae, ...  

[5 rows x 51 columns]

In [64]:
df

unique_id     hurst  \
0          artificialNoAnomaly/art_daily_no_noise.csv       NaN   
1   artificialNoAnomaly/art_daily_perfect_square_w...       NaN   
2       artificialNoAnomaly/art_daily_small_noise.csv  0.412716   
3                   artificialNoAnomaly/art_noisy.csv  0.507001   
4      artificialWithAnomaly/art_daily_flatmiddle.csv  0.501646   
5       artificialWithAnomaly/art_daily_jumpsdown.csv  0.523080   
6         artificialWithAnomaly/art_daily_jumpsup.csv  0.565294   
7          artificialWithAnomaly/art_daily_nojump.csv  0.553390   
8   artificialWithAnomaly/art_increase_spike_densi...  0.324410   
9   artificialWithAnomaly/art_load_balancer_spikes...       NaN   
10          realAdExchange/exchange-2_cpc_results.csv  0.906114   
11          realAdExchange/exchange-2_cpm_results.csv  0.720425   
12          realAdExchange/exchange-3_cpc_results.csv  0.827410   
13          realAdExchange/exchange-3_cpm_results.csv  0.898996   
14          realAdExchange/exchange-4_cpc_results.csv  0.520317   
15          realAdExchange/exchange-4_cpm_results.csv  0.390779   
16   realAWSCloudwatch/ec2_cpu_utilization_24ae8d.csv  0.542713   
17   realAWSCloudwatch/ec2_cpu_utilization_53ea38.csv       NaN   
18   realAWSCloudwatch/ec2_cpu_utilization_5f5533.csv  1.592583   
19   realAWSCloudwatch/ec2_cpu_utilization_77c1ca.csv  0.950880   
20   realAWSCloudwatch/ec2_cpu_utilization_825cc2.csv  1.023656   
21   realAWSCloudwatch/ec2_cpu_utilization_ac20cd.csv  1.089914   
22   realAWSCloudwatch/ec2_cpu_utilization_c6585a.csv       NaN   
23   realAWSCloudwatch/ec2_cpu_utilization_fe7f93.csv  0.802616   
24  realAWSCloudwatch/ec2_disk_write_bytes_1ef3de.csv       NaN   
25  realAWSCloudwatch/ec2_disk_write_bytes_c0d644.csv       NaN   
26        realAWSCloudwatch/ec2_network_in_257a54.csv  0.997192   
27        realAWSCloudwatch/ec2_network_in_5abac7.csv  0.857048   
28     realAWSCloudwatch/elb_request_count_8c0756.csv  0.838219   
29             realAWSCloudwatch/grok_asg_anomaly.csv  1.246498   
30  realAWSCloudwatch/iio_us-east-1_i-a2eb1cd9_Net...  0.692340   
31   realAWSCloudwatch/rds_cpu_utilization_cc0c53.csv  1.166369   
32   realAWSCloudwatch/rds_cpu_utilization_e47b3b.csv  1.294494   
33  realKnownCause/ambient_temperature_system_fail...  1.085836   
34  realKnownCause/ec2_request_latency_system_fail...  0.994541   
35            realKnownCause/rogue_agent_key_hold.csv  0.787292   
36          realKnownCause/rogue_agent_key_updown.csv  0.372617   
37                     realTraffic/occupancy_6005.csv  0.944087   
38                    realTraffic/occupancy_t4013.csv  1.069734   
39                         realTraffic/speed_6005.csv  1.032658   
40                         realTraffic/speed_7578.csv  1.134815   
41                        realTraffic/speed_t4013.csv  0.968274   
42                     realTraffic/TravelTime_451.csv  0.689832   

    series_length  unitroot_pp  unitroot_kpss      hw_alpha       hw_beta  \
0            4032   -45.198782       0.046765  5.000000e-01  1.000000e-04   
1            4032   -63.887428       0.043267  5.000000e-01  1.750000e-01   
2            4032   -57.839587       0.046790  1.490000e-08  1.010000e-08   
3            4032 -4126.670693       0.299753  1.580000e-08  7.610000e-09   
4            4032   -49.327420       0.121571  5.372404e-01  1.590000e-07   
5            4032   -55.541723       0.098380  2.378961e-01  2.540000e-13   
6            4032   -53.046075       0.260825  3.412410e-01  8.780000e-11   
7            4032   -52.591420       0.185286  3.270213e-01  1.100000e-10   
8            4032 -4751.528222       0.008390  1.500000e-08  1.040000e-08   
9            4032 -1639.435252       1.734170  6.502030e-01  8.840000e-07   
10           1648  -291.651096       3.322436  6.629547e-01  3.690000e-10   
11           1648  -352.407911       0.688890  4.138180e-01  1.150000e-09   
12           1647  -689.702090       0.784406  2.486063e-01  0.000000e+00   
13           1647

Stacking Appraoch to combine inputs from base model - RandomForest Regressor 

In [65]:
def stacked_model_predictions(val, base_preds):
     # Convert string inputs to lists of floats
     # Convert string inputs to lists of floats for each column in base_preds
    base_preds = [list(map(float, col.strip('[]').split(','))) for col in base_preds]
    
    # Convert lists to numpy arrays and transpose to get the correct shape
    base_preds = np.asarray(base_preds).T

    print("Type of base_preds:", type(base_preds))
    print("Shape of base_preds:", base_preds.shape)
    #val = list(map(float, val[0].strip('[]').split(',')))
    
    
    
    # Convert lists to numpy arrays
    val = np.asarray(val).reshape(-1)
    #base_preds = np.asarray(base_preds).reshape(-1, 1)
    # Check the type and shape after conversion
    print("Type of val:", type(val))
    print("Shape of val:", val.shape)
    

    # Check if base_preds and val have the same length
    if base_preds.shape[0] != len(val):
        raise ValueError("base_preds and val must have the same length.")
    # Ensure base_preds and val are numpy arrays

    
    # Check if base_preds and val have the same length
    if len(base_preds) != len(val):
        raise ValueError("base_preds and val must have the same length.")
    # Splitting features and target variable sequentially
    train_size = int(0.65 * len(val))  # Assuming the split ratio is 80-20
    X_train, y_train = base_preds[:train_size], val[:train_size]
    X_val, y_val = base_preds[train_size:], val[train_size:]

    # Define parameter grid for Random Forest
    param_grid = {
        'n_estimators': [25, 50, 100, 150, 200],  # Number of trees in the forest
        'max_depth': [None, 10, 20, 30],      # Maximum depth of the tree
        'min_samples_split': [2, 5, 8, 10, 15],  # Minimum number of samples required to split an internal node
        'min_samples_leaf': [1, 2, 4, 6]     # Minimum number of samples required to be at a leaf node
    }

    # Initialize Random Forest regressor
    rf = RandomForestRegressor(random_state=42)

    search = RandomizedSearchCV(estimator=rf, param_distributions=param_grid, n_iter=100, cv=2, scoring='neg_mean_absolute_error', n_jobs=-1, random_state=42)
    search.fit(X_train, y_train)

    print("Stacking Approach")

    # Print the best estimator found
    print(search.best_estimator_)

    # Make predictions using the best model
    y_pred = search.best_estimator_.predict(X_val)

    # Calculate Mean Absolute Error (MAE)
    mae = mean_absolute_error(y_val, y_pred)
    print("Mean Absolute Error (MAE):", mae)

    # Calculate Mean Squared Error (MSE)
    mse = mean_squared_error(y_val, y_pred)
    print("Mean Squared Error (MSE):", mse)

    # Calculate Root Mean Squared Error (RMSE)
    rmse = np.sqrt(mse)
    print("Root Mean Squared Error (RMSE):", rmse)

    # Calculate Mean Absolute Percentage Error (MAPE)
    mape = mean_absolute_percentage_error(y_val, y_pred)
    print("Mean Absolute Percentage Error (MAPE):", mape)

    print("")

    return y_pred, y_val, mae, mse, rmse, mape


In [66]:
# Create an empty column named 'ensemble_size'
df['ensemble_size'] = np.nan
# Display the DataFrame with the new empty column
df.head(2)

unique_id  hurst  series_length  \
0         artificialNoAnomaly/art_daily_no_noise.csv    NaN           4032   
1  artificialNoAnomaly/art_daily_perfect_square_w...    NaN           4032   

   unitroot_pp  unitroot_kpss  hw_alpha  hw_beta  hw_gamma     stability  \
0   -45.198782       0.046765       0.5   0.0001      0.25  1.050000e-62   
1   -63.887428       0.043267       0.5   0.1750      0.20  0.000000e+00   

   nperiods  ...  seas_acf1  exponential_smoothing   xgboost  random_forest  \
0         1  ...   0.928571              26.762319  0.012269       0.003747   
1         1  ...   0.928571              27.341756  0.010629       0.000028   

        gru       vae      lstm        gan  \
0  0.609464  1.559429  0.707946  10.602318   
1  0.558414  1.410600  0.414601   3.206596   

                                          model_rank  ensemble_size  
0  [random_forest, xgboost, gru, lstm, vae, gan, ...            NaN  
1  [random_forest, xgboost, lstm, gru, vae, gan, ...            NaN  

[2 rows x 52 columns]

Logic to find the appropriate ensemble size for training

In [67]:
def find_ensemble_size(model_rank, unique_id, predicted_df_final, mae_df_final, original_values_df):

    threshold_mape=0.05
    # Extract directory and file name from unique_id
    dir_name, file_name = unique_id.split('/')

    # Get the first element from the list of model_rank
    model_name = model_rank[0]

    # Find the row in mae_df dataframe that matches the directory and file name
    row = mae_df_final[(mae_df_final['dir'] == dir_name) & (mae_df_final['file_name'] == file_name)]

    # Find the value in the column that matches the model_name
    model_mae = row[model_name].iloc[0]

    # Determine the ensemble size based on the model MAE value
    if model_mae < threshold_mape:
        print(f"No need for stacking approach, since the first model {model_name} has MAE value {model_mae} less than the threshold value {threshold_mape}")
        return 1
    else:
        previous_mae = model_mae
        print("Going for stacking Approach")
        i = 1  # Initialize the count of models
        while i < len(model_rank):
            print("Going for the next iteration ", i+1, " of the same loop")
            threshold_mape=threshold_mape+0.03
            i += 1  # Increment the count of models
            models_to_use = model_rank[:i]  # Take the first i models from the model_rank list
            base_preds = []  # Initialize base_preds as a list
            # Get the predicted values for the selected models
            for model in models_to_use:
                # Find the respective row in predicted_df
                model_row = predicted_df_final[(predicted_df_final['dir'] == dir_name) & (predicted_df_final['file_name'] == file_name)]
                # Get the predicted value for the model
                pred_value = model_row[model].iloc[0]

                print(pred_value)
                # Append the predicted value to base_preds
                base_preds.append(pred_value)

            val_row = original_values_df[(original_values_df['dir'] == dir_name) & (original_values_df['file_name'] == file_name)]
            val = val_row['values'].iloc[0]

            base_preds = np.stack(base_preds, axis=-1)
            y_pred, y_val, mae, mse, rmse, mape = stacked_model_predictions(val, base_preds)

            if mae > previous_mae:
                if i!=2:
                    print("MAE increased after adding", i, "models, from", previous_mae, "to", mae, "so returning the previous ensemble size")
                    return i - 1

            # Update previous MAE with current MAE
            previous_mae = mae

            # If MAE is less than 0.05, return the current ensemble size
            if mae < threshold_mape:
                return i        

    # If none of the models have MAE less than 0.05, return the total count of models
    return len(model_rank)

In [68]:
for index, row in df.iterrows():
    # Extract values from the current row
    model_rank = row['model_rank']
    unique_id = row['unique_id']

    # Print the unique ID before calling the function
    print("Unique ID:", unique_id)

    # Call the function to find ensemble size
    ensemble_size = find_ensemble_size(model_rank, unique_id, predicted_df_final, mae_df_final, original_values_df)

    print("")

    # Assign the ensemble size to the 'ensemble_size' column
    df.at[index, 'ensemble_size'] = ensemble_size

Unique ID: artificialNoAnomaly/art_daily_no_noise.csv
No need for stacking approach, since the first model random_forest has MAE value 0.0037471047465226 less than the threshold value 0.05

Unique ID: artificialNoAnomaly/art_daily_perfect_square_wave.csv
No need for stacking approach, since the first model random_forest has MAE value 2.78025920983803e-05 less than the threshold value 0.05

Unique ID: artificialNoAnomaly/art_daily_small_noise.csv
Going for stacking Approach
Going for the next iteration  2  of the same loop
[69.05628204345703, 69.05628204345703, 69.05628204345703, 69.05628204345703, 69.05628204345703, 76.02310180664062, 76.02310180664062, 76.02310180664062, 76.02310180664062, 76.02310180664062, 76.02310180664062, 76.02310180664062, 76.02310180664062, 76.02310180664062, 76.02310180664062, 76.02310180664062, 76.02310180664062, 79.04875183105469, 79.04875183105469, 79.04875183105469, 79.04875183105469, 79.04875183105469, 79.04875183105469, 79.04875183105469, 79.048751831054

Stacking Approach
RandomForestRegressor(max_depth=10, min_samples_split=15, n_estimators=200,
                      random_state=42)
Mean Absolute Error (MAE): 2.1730250918319425
Mean Squared Error (MSE): 8.802015111937378
Root Mean Squared Error (RMSE): 2.9668190224443043
Mean Absolute Percentage Error (MAPE): 0.051392557392609464

Going for the next iteration  3  of the same loop
[69.05628204345703, 69.05628204345703, 69.05628204345703, 69.05628204345703, 69.05628204345703, 76.02310180664062, 76.02310180664062, 76.02310180664062, 76.02310180664062, 76.02310180664062, 76.02310180664062, 76.02310180664062, 76.02310180664062, 76.02310180664062, 76.02310180664062, 76.02310180664062, 76.02310180664062, 79.04875183105469, 79.04875183105469, 79.04875183105469, 79.04875183105469, 79.04875183105469, 79.04875183105469, 79.04875183105469, 79.04875183105469, 79.04875183105469, 79.04875183105469, 79.04875183105469, 79.04875183105469, 80.74359893798828, 80.74359893798828, 80.74359893798828, 80.743

In [69]:
# Display the updated DataFrame
df

unique_id     hurst  \
0          artificialNoAnomaly/art_daily_no_noise.csv       NaN   
1   artificialNoAnomaly/art_daily_perfect_square_w...       NaN   
2       artificialNoAnomaly/art_daily_small_noise.csv  0.412716   
3                   artificialNoAnomaly/art_noisy.csv  0.507001   
4      artificialWithAnomaly/art_daily_flatmiddle.csv  0.501646   
5       artificialWithAnomaly/art_daily_jumpsdown.csv  0.523080   
6         artificialWithAnomaly/art_daily_jumpsup.csv  0.565294   
7          artificialWithAnomaly/art_daily_nojump.csv  0.553390   
8   artificialWithAnomaly/art_increase_spike_densi...  0.324410   
9   artificialWithAnomaly/art_load_balancer_spikes...       NaN   
10          realAdExchange/exchange-2_cpc_results.csv  0.906114   
11          realAdExchange/exchange-2_cpm_results.csv  0.720425   
12          realAdExchange/exchange-3_cpc_results.csv  0.827410   
13          realAdExchange/exchange-3_cpm_results.csv  0.898996   
14          realAdExchange/exchange-4_cpc_results.csv  0.520317   
15          realAdExchange/exchange-4_cpm_results.csv  0.390779   
16   realAWSCloudwatch/ec2_cpu_utilization_24ae8d.csv  0.542713   
17   realAWSCloudwatch/ec2_cpu_utilization_53ea38.csv       NaN   
18   realAWSCloudwatch/ec2_cpu_utilization_5f5533.csv  1.592583   
19   realAWSCloudwatch/ec2_cpu_utilization_77c1ca.csv  0.950880   
20   realAWSCloudwatch/ec2_cpu_utilization_825cc2.csv  1.023656   
21   realAWSCloudwatch/ec2_cpu_utilization_ac20cd.csv  1.089914   
22   realAWSCloudwatch/ec2_cpu_utilization_c6585a.csv       NaN   
23   realAWSCloudwatch/ec2_cpu_utilization_fe7f93.csv  0.802616   
24  realAWSCloudwatch/ec2_disk_write_bytes_1ef3de.csv       NaN   
25  realAWSCloudwatch/ec2_disk_write_bytes_c0d644.csv       NaN   
26        realAWSCloudwatch/ec2_network_in_257a54.csv  0.997192   
27        realAWSCloudwatch/ec2_network_in_5abac7.csv  0.857048   
28     realAWSCloudwatch/elb_request_count_8c0756.csv  0.838219   
29             realAWSCloudwatch/grok_asg_anomaly.csv  1.246498   
30  realAWSCloudwatch/iio_us-east-1_i-a2eb1cd9_Net...  0.692340   
31   realAWSCloudwatch/rds_cpu_utilization_cc0c53.csv  1.166369   
32   realAWSCloudwatch/rds_cpu_utilization_e47b3b.csv  1.294494   
33  realKnownCause/ambient_temperature_system_fail...  1.085836   
34  realKnownCause/ec2_request_latency_system_fail...  0.994541   
35            realKnownCause/rogue_agent_key_hold.csv  0.787292   
36          realKnownCause/rogue_agent_key_updown.csv  0.372617   
37                     realTraffic/occupancy_6005.csv  0.944087   
38                    realTraffic/occupancy_t4013.csv  1.069734   
39                         realTraffic/speed_6005.csv  1.032658   
40                         realTraffic/speed_7578.csv  1.134815   
41                        realTraffic/speed_t4013.csv  0.968274   
42                     realTraffic/TravelTime_451.csv  0.689832   

    series_length  unitroot_pp  unitroot_kpss      hw_alpha       hw_beta  \
0            4032   -45.198782       0.046765  5.000000e-01  1.000000e-04   
1            4032   -63.887428       0.043267  5.000000e-01  1.750000e-01   
2            4032   -57.839587       0.046790  1.490000e-08  1.010000e-08   
3            4032 -4126.670693       0.299753  1.580000e-08  7.610000e-09   
4            4032   -49.327420       0.121571  5.372404e-01  1.590000e-07   
5            4032   -55.541723       0.098380  2.378961e-01  2.540000e-13   
6            4032   -53.046075       0.260825  3.412410e-01  8.780000e-11   
7            4032   -52.591420       0.185286  3.270213e-01  1.100000e-10   
8            4032 -4751.528222       0.008390  1.500000e-08  1.040000e-08   
9            4032 -1639.435252       1.734170  6.502030e-01  8.840000e-07   
10           1648  -291.651096       3.322436  6.629547e-01  3.690000e-10   
11           1648  -352.407911       0.688890  4.138180e-01  1.150000e-09   
12           1647  -689.702090       0.784406  2.486063e-01  0.000000e+00   
13           1647

In [70]:
# Assuming df_features is your DataFrame

# Convert 'ensemble_size' column from float to integer
df['ensemble_size'] = df['ensemble_size'].astype(int)

# Print the DataFrame to verify the changes
df.head(5)

unique_id     hurst  series_length  \
0         artificialNoAnomaly/art_daily_no_noise.csv       NaN           4032   
1  artificialNoAnomaly/art_daily_perfect_square_w...       NaN           4032   
2      artificialNoAnomaly/art_daily_small_noise.csv  0.412716           4032   
3                  artificialNoAnomaly/art_noisy.csv  0.507001           4032   
4     artificialWithAnomaly/art_daily_flatmiddle.csv  0.501646           4032   

   unitroot_pp  unitroot_kpss      hw_alpha       hw_beta      hw_gamma  \
0   -45.198782       0.046765  5.000000e-01  1.000000e-04  2.500000e-01   
1   -63.887428       0.043267  5.000000e-01  1.750000e-01  2.000000e-01   
2   -57.839587       0.046790  1.490000e-08  1.010000e-08  3.110000e-21   
3 -4126.670693       0.299753  1.580000e-08  7.610000e-09  2.480000e-06   
4   -49.327420       0.121571  5.372404e-01  1.590000e-07  2.630000e-07   

      stability  nperiods  ...  seas_acf1  exponential_smoothing    xgboost  \
0  1.050000e-62         1  ...   0.928571              26.762319   0.012269   
1  0.000000e+00         1  ...   0.928571              27.341756   0.010629   
2  1.280000e-05         1  ...   0.918527              25.923756   2.283104   
3  5.353556e-03         1  ...   0.005106               2.800236   2.785615   
4  1.456821e-02         1  ...   0.833093              39.576025  10.404284   

   random_forest       gru        vae      lstm        gan  \
0       0.003747  0.609464   1.559429  0.707946  10.602318   
1       0.000028  0.558414   1.410600  0.414601   3.206596   
2       2.199849  2.599541   3.569074  2.668343   5.901315   
3       2.883937  2.823385   2.805615  2.778922   3.105839   
4      10.448658  7.000000  14.631948  4.452525   8.156758   

                                          model_rank  ensemble_size  
0  [random_forest, xgboost, gru, lstm, vae, gan, ...              1  
1  [random_forest, xgboost, lstm, gru, vae, gan, ...              1  
2  [random_forest, xgboost, gru, lstm, vae, gan, ...              4  
3  [lstm, xgboost, exponential_smoothing, vae, gr...              2  
4  [lstm, gru, gan, xgboost, random_forest, vae, ...              3  

[5 rows x 52 columns]

In [71]:
# Delete the row with index 3
df = df.drop(index=3)

In [72]:


# Save the DataFrame
df.to_csv('../dataset_preparation/df_features_with_ensemble_size_2.csv', index=False)  # for CSV file

print("CSV saved successfully")

CSV saved successfully
